# **Análise Exploratória dos Hábitos de Jogo dos Jogadores de Valorant**

## Configurações Iniciais

### Imports

In [41]:
import os
import sys
from pyspark.sql import SparkSession
from pyspark.sql.functions import avg, col, expr, count, sum, max, udf, dayofweek, date_format, when, mean, median
from pyspark.sql.types import StringType
sys.path.append('../src/')
from aws.aws import Aws
import io
import pandas as pd 
import boto3
from datetime import datetime
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.express as px
import warnings
warnings.filterwarnings("ignore")

### Criando a seção Spark

In [42]:
spark = SparkSession.builder.appName("ValorantDataAnalysis").getOrCreate()

In [43]:
spark.conf.set("spark.hadoop.fs.s3a.impl", "org.apache.hadoop.fs.s3a.S3AFileSystem")
spark.conf.set("spark.hadoop.fs.s3a.access.key", os.getenv('AWS_ACCESS_KEY_ID'))
spark.conf.set("spark.hadoop.fs.s3a.secret.key", os.getenv('AWS_SECRET_ACCESS_KEY'))

### Config pandas.

In [88]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
# Configurar o formato dos números
pd.set_option('display.float_format', '{:.2f}'.format)

### Instânciando as classe utilizadas.

In [45]:
aws = Aws()

## Carregando os dataframes.

### Utils.

In [46]:
def get_files(bucket_name : str, folder_path : str) -> list:
    """"""
    objects = aws.list_objetcs_s3(bucket_name, folder_path)


    return objects

def concat_files_s3(objects):
    """"""

    json_files = [obj['Key'] for obj in objects]

    for file in json_files:

        response = aws.read_s3_v2(bucket_name='s3-tcc-fia-valorant', folder_path=file)
        json_data = response['Body'].read().decode('utf-8')

    return io.StringIO(json_data)

def read_spark(data_io):
    """"""
    data_io = pd.read_csv(data_io)
    return spark.createDataFrame(data_io)

def create_dataframe(bucket_name : str, folder_path : str):
    """"""
    objects = get_files(bucket_name, folder_path)
    data_io = concat_files_s3(objects)
    df = read_spark(data_io)

    return df

def save_dataframe_csv(bucket_name, folder_path, file_name, data, file_format):
    # Convert DataFrame to CSV string
    csv_buffer = io.StringIO()
    data.toPandas().to_csv(csv_buffer, index=False)

    # Retrieve CSV data from buffer
    csv_buffer_value = csv_buffer.getvalue()

    date = datetime.now().strftime("%Y%m%d_%H%M%S")
    file_name = file_name + '_' + date + file_format
    file_path = folder_path + file_name

    # Write CSV string to S3
    s3 = boto3.resource('s3')

    try:
        s3.Object(bucket_name, file_path).put(Body=csv_buffer_value)
        print(f"Data was written to S3://{bucket_name}/{folder_path}")

    except Exception as e:

        print(f"Error: {e}")
    
        return False



### df_player_book

In [71]:
df_player_book = create_dataframe('s3-tcc-fia-valorant', 'valorant/refined/player-book/')

## EDA

### Filtros

In [72]:
total_matches_before = df_player_book.select('match_id').distinct().count()
df_player_book = df_player_book.dropna()
total_matches_after = df_player_book.select('match_id').distinct().count()
total_matches_removed = total_matches_before - total_matches_after
print(f"Total de partidas antes da remoção dos valores nulos: {total_matches_before}")
print(f"TTotal de partidas depois da remoção dos valores nulos: {total_matches_after}")
print(f"Total matches removed: {total_matches_removed}")

Total de partidas antes da remoção dos valores nulos: 298
TTotal de partidas depois da remoção dos valores nulos: 218
Total matches removed: 80


In [73]:
total_matches_before = df_player_book.select('match_id').distinct().count()
df_player_book = df_player_book.where((col("total_players_match") == 10) & (col("total_players_team") == 5))
total_matches_after = df_player_book.select('match_id').distinct().count()
total_matches_removed = total_matches_before - total_matches_after
print(f"Total matches before removing null values: {total_matches_before}")
print(f"Total matches after removing null values: {total_matches_after}")
print(f"Total matches removed: {total_matches_removed}")

Total matches before removing null values: 218
Total matches after removing null values: 212
Total matches removed: 6


### Partidas

In [74]:
df_player_book_pd = df_player_book.toPandas()

In [ ]:
df_matches_raw_describe = df_player_book_pd.describe()
df_matches_raw_describe_pivot = pd.pivot_table(df_matches_raw_describe, columns=["count", 'mean', 'std', 'min', '25%', '50%', '75%', 'max'])
df_matches_raw_describe_pivot

#### Dias

In [76]:
df_player_book_pd_distinct = df_player_book_pd.drop_duplicates(subset=['match_id'])

In [77]:
matches_per_day = (
    
                    df_player_book_pd_distinct.groupby([df_player_book_pd_distinct.date_match, df_player_book_pd_distinct.week_day])['match_id']
                    .count()
                    .reset_index(name='count')
                    .reset_index(drop = True)
                    )
fig = px.bar(x = matches_per_day['date_match'], y = matches_per_day['count'], title= 'Numero de partidas por dia.')
fig.show()

In [78]:
weekDayOrdered = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']
mean_matches_per_days_week = (
                                matches_per_day.groupby(matches_per_day.week_day)['count']
                                .mean()
                                .reindex(weekDayOrdered) 
                                .reset_index(name = 'mean')
                                .reset_index(drop = True)
                                .round(3)
                                )

fig = px.line(mean_matches_per_days_week, x = 'week_day', y = 'mean', title = 'Média de partidas por dia.')
fig.show()

In [79]:
means_time_matches = df_player_book_pd_distinct[['match_id', 'week_day', 'playtime_minutes_value']]
means_time_matches = (
                        means_time_matches.groupby('week_day')['playtime_minutes_value']
                        .mean()
                        .reindex(weekDayOrdered)
                        .reset_index(name = 'mean')
                        .reset_index(drop = True)                     
                        .round(2)
)

fig = px.line(means_time_matches, x = 'week_day', y = 'mean', title = 'Média de tempo jogado por dia da semana.')
fig.show()

In [80]:
top_seven_days_matches = (
                            df_player_book_pd_distinct.groupby(['date_match', 'week_day'])['week_day']
                            .count()
                            .reset_index(name = 'count')
                            .sort_values('count', ascending = False)
                            .reset_index(drop = True)
                            .head(7)
                            )
fig = px.bar(top_seven_days_matches, x='week_day', y='count',
             hover_data=['date_match', 'count'], color='count', height=400, title = 'Top sete dias por quantidade de partidas.')
fig.show()

**Análise Exploratória dos Hábitos de Jogo dos Jogadores de Valorant**

A análise exploratória revelou números significativos sobre os hábitos de jogo dos jogadores de Valorant. Ao longo da semana, os jogadores realizam em média **1,75 a 2,22 jogos por dia**. Essa variação é evidente ao observar as médias de jogos por dia da semana:

**Quartas-feiras, quintas-feiras e sábados** registram cerca de **1,8 jogos**.
**Segundas e sextas-feiras** têm aproximadamente **1,73** a **1,80 jogos**.
As **terças-feiras** apresentam a **média mais baixa**, com **1,75 jogos**.
No entanto, os **domingos se destacam** com a **média mais alta** de **2,22 jogos**.
Além disso, é importante ressaltar alguns dias específicos com números expressivos de jogos. O dia **19/12/2022 (segunda-feira)** e o dia **01/05/2022 (domingo)** registraram um total de **5 jogos cada**. Já os dias **12/05/2023 (sexta-feira) e 06/05/2023 (sábado)** contabilizaram **4 jogos cada**.

Esses números destacados indicam momentos de maior participação dos jogadores, **sugerindo a ocorrência de eventos especiais**, torneios ou outras atividades que estimularam a **intensificação do engajamento dos jogadores**.

Esses insights podem orientar a **alocação de recursos e a implementação de iniciativas** direcionadas para maximizar o engajamento dos jogadores de Valorant.

#### Plantio e desarmamento da spike

In [81]:
matches_plat_defuse = (
                        df_player_book_pd_distinct.groupby(['result'])[['plants_value', 'defuses_value']]
                        .sum()
                        .sort_values('plants_value', ascending = False)
                        .reset_index()
)

fig = px.bar(matches_plat_defuse, x = 'result', y = 'plants_value', text_auto='.2s',
            title="Default: various text sizes, positions and angles", color = 'result')
fig.show()

fig = px.bar(matches_plat_defuse, x = 'result', y = 'defuses_value', text_auto='.2s',
            title="Default: various text sizes, positions and angles", color = 'result')
fig.show()

fig = go.Figure()
fig.add_trace(go.Box(y=matches_plat_defuse['plants_value'],
                    name='plantsValue'))
fig.add_trace(go.Box(y=matches_plat_defuse['defuses_value'],
                    name='defusesValue'))
fig.show()

Em média, **equipes vitoriosas** plantaram a spike **135 vezes** e desarmaram **37 vezes**.
Equipes que **sofreram derrotas** plantaram a spike **130 vezes** e desarmaram **46 vezes**.
**Em empates**, ocorreram apenas **6 plantios da spike** e **nenhum** desarme.
Esses dados destacam a **importância dos plantio e desarmes** para o resultado das partidas de Valorant. Equipes com um **alto número de plantas e desarmes** têm uma **maior probabilidade de alcançar a vitória**. Portanto, é crucial para os jogadores e equipes desenvolverem estratégias eficientes para essas ações dentro do jogo.

#### Mapas

In [58]:
maps_matches = df_player_book_pd_distinct[['match_id', 'map_name']]
maps_matches = (
                maps_matches.groupby('map_name')['match_id']
                .count()
                .reset_index(name='count')
                .reset_index(drop=True)
                .sort_values('count', ascending = True)

)

fig = px.bar(maps_matches, x='map_name', y='count', title='Numero de partidas por mapa.')
fig.show()


Observa-se que o mapa **Haven possui o maior número de partidas**, com um total de **39**. Em seguida, temos os mapas **Ascent** e **Bind** com **37 partidas**, respectivamente. Por outro lado, os mapas **Breeze** e **Fracture**, ambos com **18 partidas**, apresentam uma quantidade menor de partidas registradas.

É **importante ressaltar** que a quantidade de partidas pode estar relacionada à **popularidade e tempo de existência dos mapas**. Os mapas **mais antigos**, como **Haven, "Ascent e Bind**, têm mais tempo para acumular partidas em comparação com os mapas **mais recentes**, como **Breeze e Fracture**. Portanto, a distribuição reflete não apenas a preferência dos jogadores, mas também a idade dos mapas, sendo esperado que os mapas mais novos aumentem sua quantidade de partidas ao longo do tempo.

Vale lembrar que em Valorant a **Riot** tenta garantir uma **distribuição igualitaria** entre os mapas como podemos ver nos mais antigos.

#### Rounds

In [109]:
df_player_book_pd_distinct.head(2)

match_id platform_user_identifier   
0   01f95d78-c404-4c9f-9a27-22b54f1fdf1c             Makitori#BR1  \
10  4ad95277-c731-4f7d-b826-e173e458278e    Ambulância de AK#duda   

    total_spent_credits  total_rounds rank_value current_rank_value   
0              32550.00            17   Bronze 3           Silver 3  \
10             59650.00            19     Gold 3           Silver 3   

    score_value  score_per_round_value  kills_per_round_value  kills_value   
0          4282                 251.88                   0.94           16  \
10         6718                 353.58                   1.26           24   

    deaths_value  assists_value  kd_ratio_value  damage_value   
0             10              2            1.60          2858  \
10            14             11            1.71          3960   

    damage_per_round_value  damage_delta_per_round_value  single_kills_value   
0                   168.12                         59.00                   5  \
10                  208.42                         50.58                   4   

    double_kills_value  triple_kills_value  quadra_kills_value   
0                    4                   1                   0  \
10                   7                   2                   0   

    penta_kills_value  multi_kills_value  grenade_casts_value   
0                   0                  1                16.00  \
10                  0                  2                14.00   

    ability1_casts_value  ability2_casts_value  ultimate_casts_value   
0                   5.00                  9.00                  2.00  \
10                 20.00                 10.00                  3.00   

    grenade_casts_per_round_value  ability1_casts_per_round_value   
0                            0.94                            0.29  \
10                           0.74                            1.05   

    ability2_casts_per_round_value  ultimate_casts_per_round_value   
0                             0.53                            0.12  \
10                            0.53                            0.16   

    plants_value  defuses_value  first_kills_value  first_deaths_value   
0              1              1                  3                   0  \
10             5              0                  5                   3   

    esr_value  first_kills_per_round_value  first_deaths_per_round_value   
0      100.00                         0.18                          0.00  \
10      62.50                         0.26                          0.16   

    econ_rating_value  hs_accuracy_value  kast_value  clutches_value   
0                  89              27.27       71.00               1  \
10                 67              16.46       89.00               1   

    rounds_win_pct_value  trn_performance_score_value   
0                  76.47                          834  \
10                 68.42                          992   

                                party_id team_id agent_name  has_won   
0   f6aa7b58-3bd2-4b33-8a02-56c2baa8a23f    Blue    Chamber     True  \
10  08507048-52c1-4e9d-a5b1-a392a4d92882     Red       Sage     True   

    rounds_won_value  rounds_lost_value  team_score_value  team_kills_value   
0                 13                  4             20989                75  \
10                13                  6             22075                76   

    team_deaths_value  team_assists_value  team_damage_value weapon_name   
0                  49                  27              13406      Vandal  \
10                 63                  41              14384      Vandal   

    max_total_kills_weapon_name  is_available                      timestamp   
0                             8          True  2022-10-21T20:09:55.848+00:00  \
10                           15          True  2022-12-21T19:21:26.283+00:00   

   season_name map_name  playtime_value   result   
0       E5: A3   Ascent            1635  victory  \
10      E5: A3    Pearl            20

In [115]:
df = df_player_book_pd_distinct[["total_rounds", "result"]]
fig = px.histogram(df, x="total_rounds", color="result", barmode="group", title="Distribuição dos Rounds por Resultado")
fig.show()


In [107]:
rounds_matches = df_player_book_pd_distinct[['match_id', 'total_rounds', 'result']]
rounds_matches = (
                rounds_matches.groupby('match_id')['total_rounds']
                .max()
                .reset_index(name='max')
                .reset_index(drop=True)
                .sort_values('max', ascending = False)
                .head(10)

)

fig = px.bar(rounds_matches, x='match_id', y='max', title='Numero de partidas por mapa.')
fig.show()


In [108]:
rounds_matches

match_id  max
94   78467f93-0043-4b55-b96b-10cfc580ac2c   30
161  c4a81f66-a5c2-4618-a079-383a4bbc2ef9   30
209  fd9942aa-5926-4117-997c-0dc0a1aaf3e7   30
9    09d2bcfc-5625-4fe1-ad6a-f3d2edff4f89   28
185  e3540d14-9ed6-4e3f-be81-689fbd0b4b19   28
45   3f7ebebb-88fd-4832-a349-fdaed8ae5e81   28
202  f780e0df-0539-4721-bc05-c430c90c03a3   28
152  ba6b133a-6ae9-4a11-ac54-265aef894038   28
73   6128814b-725e-4a7e-a713-849c99466b04   28
80   692dde2b-4d82-47c1-a930-11bcb71fb756   28

In [105]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=number_kda_agent['agentName'], y=number_kda_agent['killsValue'],
                    mode='lines',
                    name='killsValue'))
fig.add_trace(go.Scatter(x=number_kda_agent['agentName'], y=number_kda_agent['deathsValue'],
                    mode='lines',
                    name='deathsValue'))
fig.add_trace(go.Scatter(x=number_kda_agent['agentName'], y=number_kda_agent['assistsValue'],
                    mode='lines',
                    name='assistsValue'))

fig.show()

AttributeError: 'SeriesGroupBy' object has no attribute 'avg'

In [89]:
df_player_book_pd_distinct

match_id platform_user_identifier   
0     01f95d78-c404-4c9f-9a27-22b54f1fdf1c             Makitori#BR1  \
10    4ad95277-c731-4f7d-b826-e173e458278e    Ambulância de AK#duda   
20    94bbbb3c-2e1f-4546-a7a6-49bbc8aa6936               Apollo#top   
30    06b77f0e-32a3-4088-aebb-145ced489229     Cap Nascimento#Capta   
40    259a5a1e-e0a8-420f-97bd-6e2411640b46              Carlos#0000   
50    5e54de80-9c49-458b-9e15-1d5ed1b200c4           LótusWhite#BR1   
60    4cf7b8c7-6862-47ed-b7a1-ab9ed57cc60d          Arroz Catua#txt   
70    19afa9a9-4b08-4cf7-bef1-c599c8f98b06            AL THEUS#7699   
80    42848f0a-861f-4d9e-acd4-9c663e7d518a           Andarcness#BR1   
90    997d0ee6-e2da-4d3c-8313-10628baef9f2               FR0ST#7853   
100   a81ff86a-d7e2-4710-83e6-24e30d499e68     Chupeta Mago Vei#BR7   
110   a8713cc0-c452-4500-9be8-193ffa667df3         Capuchovisky#BR1   
120   fb2811fc-844b-49af-bca6-308d2bd4a7e2               Coral#Hebi   
130   cddedd61-90c0-4e67-8bae-a97c63f51717             Erasure#2022   
140   c6b5dd73-e8b6-48b8-8c00-b4ade768666f         APG LeozinxD#BR1   
150   2def2e7e-2933-46a0-80f6-517cdf3cfec1              Aemond#f1br   
160   7a516b69-739a-425e-8d03-006e1c2be6f8    BLACK LÓTUS    ツ#uhum   
170   294be43e-77ac-47ae-b438-f7d0bbb09e9e            000000098#BR1   
180   c5127c1a-b935-4b32-aa9c-db2a6249dbbb              Bragets#BR1   
190   f68f3277-b067-4788-b36b-26cfa1d47ad1                  A12#WOB   
200   0c3f41ce-2af0-4108-918b-20866ccb517d               Arkran#BR1   
210   2cb6a125-6755-42fc-95c2-bbd2d590179e       JEF3RS0NTRUCKS#BR1   
220   927f0f65-c0ce-4943-9000-13a9e2ebcfc5         Como é abigo#BR1   
230   673da594-bbd2-43be-bf5c-3a01d983480c             Glauber#4706   
240   b8f5a541-5424-4d3e-aa71-02752801b30b               Drake#8287   
250   0b171f6a-ef53-40f9-ae2b-12e043af8747        Bebeloco1456#1000   
260   ecc55239-3f98-473b-8302-b2878811a436        IIchabodCrane#BR1   
270   810c3759-e822-4e21-a1de-71af5628b5c6            Filipefuj#fuj   
280   ba6b133a-6ae9-4a11-ac54-265aef894038              Cloudyz#BR1   
290   e9db2009-db07-4064-879d-1eff7ec0f8da              Freshz#1618   
300   128e8305-2992-49d0-99e3-8682025773d4               Anna么#anna   
310   af438923-f614-47d3-9de6-c20a6c7f4256        Cubano Mortem#BR1   
320   746a5698-10c5-41b7-b92f-0768b391db2b        4k JGGamerTV#5095   
330   23b8a2b8-fe9e-4d51-a518-9fded2718d6a         ALM Malvadão#BR1   
340   3f511b1e-b5f1-4cae-a8bc-e2ff010caa25       Eu sou Groot#Livre   
350   4f833dee-64b3-430f-a9a3-d3d7d1351312        GustavoPool69#117   
360   2f9daeba-4a7e-4ca6-81e5-46edda679499        DRSJULIALINDA#BR1   
370   b9e04e57-59d8-4704-b966-7a1453562a1d      0dln semi boss#0030   
380   30e0189b-0dd3-4e25-bda3-aa47927a84eb              COREANO#C 4   
390   9b3df458-fd72-4ad8-8ade-9d91f11a444b               Birlø#2141   
400   bdec149a-b4b3-4aa0-97ce-04155d07d727              Aemond#f1br   
410   fe3dbe25-7dd3-468b-be9b-250833913e40      DominicTorreta#3636   
420   c7040177-9de1-45cf-8bc6-91e7eba984f2     Joaquin Phoenix#0420   
430   1de1383e-f6d6-49a8-82ca-fd55551112ff             Dollynho#001   
440   9d034b38-627f-43f9-a563-3f3d0ad0eb1d              Bragets#BR1   
450   0a933388-9c9e-4d7e-ba1a-b21dc87c621d               Anix#Annie   
460   44461b55-8c3d-45b3-afa8-d8927567c33f             AGRONrex#BR1   
470   7d54e2da-876b-4bb1-87a2-40b7779783e1                 Cliv#BR1   
480   9626a5a3-8a30-45c7-b209-2496fc277e75     BGOD mira n3gra#MLHA   
490   5a46cf29-310a-455a-9183-3a992db9f53f            Darckmeg#1380   
500   57ff15f0-bd8f-4354-94fa-25a94d0ea4b9          Chitãozinho#rox   
510   b4fc422c-2aaf-4509-9483-30482057cfda        Dona carminha#BR1   
520   bcd2b6ca-c4d2-4c93-8704-57513d9b6c67    Dobrador d leite#gozo   
530   d76e4592-ca18-4bf4-a89f-2036e520f18a      Daboss Cansogme#BR1   
540   50d20626-8aae-487e-a2c4-fa3160e42074          ARRAXCANETA#777   
550   64e650e3-5099-4298-8e31-6dc46c5388a4                

### Jogador

In [85]:
matches_per_player = (
                        df_player_book_pd.groupby(['platform_user_identifier'])['platform_user_identifier']
                        .count()
                        .reset_index(name = 'count')
                        .reset_index(drop = True)
                        .sort_values('count', ascending = False)
                        .head(10)
                        )
fig = px.line(matches_per_player, x = 'platform_user_identifier', y = 'count', title = 'Top 10 numero de partidas por jogador.')
fig.show()

Observa-se que a contagem de partidas para o jogador **RayzenSama#6999** é significativamente **maior em comparação aos demais** jogadores da lista, devido ao **processo de aquisição dos dados** estar amarrado ao ID desse jogador. Isso pode afetar a representatividade dos resultados em relação a outros jogadores.
É importante ressaltar que a quantidade de partidas está relacionada à **proximidade com o jogador RayzenSama#6999**. Dessa forma, jogadores com uma **contagem maior** de partidas têm uma maior **relação ou interação** com o jogador **RayzenSama#6999** no contexto da amostra analisada.

In [86]:
df_player_book_pd

match_id platform_user_identifier   
0     01f95d78-c404-4c9f-9a27-22b54f1fdf1c             Makitori#BR1  \
1     01f95d78-c404-4c9f-9a27-22b54f1fdf1c       PiKaRoSaUrOReX#BR1   
2     01f95d78-c404-4c9f-9a27-22b54f1fdf1c            Pizza B0Y#BR1   
3     01f95d78-c404-4c9f-9a27-22b54f1fdf1c          RayzenSama#6999   
4     01f95d78-c404-4c9f-9a27-22b54f1fdf1c           Soska Rego#BR1   
5     01f95d78-c404-4c9f-9a27-22b54f1fdf1c         borderlinda#6969   
6     01f95d78-c404-4c9f-9a27-22b54f1fdf1c         coroarantes#8862   
7     01f95d78-c404-4c9f-9a27-22b54f1fdf1c         esquisofofa#6969   
8     01f95d78-c404-4c9f-9a27-22b54f1fdf1c                  mex#xxx   
9     01f95d78-c404-4c9f-9a27-22b54f1fdf1c                 なおみ#1073   
10    4ad95277-c731-4f7d-b826-e173e458278e    Ambulância de AK#duda   
11    4ad95277-c731-4f7d-b826-e173e458278e              Chakall#ckl   
12    4ad95277-c731-4f7d-b826-e173e458278e            Pizza B0Y#BR1   
13    4ad95277-c731-4f7d-b826-e173e458278e          RayzenSama#6999   
14    4ad95277-c731-4f7d-b826-e173e458278e              SirYeah#BR1   
15    4ad95277-c731-4f7d-b826-e173e458278e              faahzin#BR1   
16    4ad95277-c731-4f7d-b826-e173e458278e         ll Dante ll#2077   
17    4ad95277-c731-4f7d-b826-e173e458278e       sou ruim mesmo#lol   
18    4ad95277-c731-4f7d-b826-e173e458278e             stargirl#lua   
19    4ad95277-c731-4f7d-b826-e173e458278e             typhoon#1057   
20    94bbbb3c-2e1f-4546-a7a6-49bbc8aa6936               Apollo#top   
21    94bbbb3c-2e1f-4546-a7a6-49bbc8aa6936              Denker#4560   
22    94bbbb3c-2e1f-4546-a7a6-49bbc8aa6936            INNaaSUS#In41   
23    94bbbb3c-2e1f-4546-a7a6-49bbc8aa6936               Kαισh#1993   
24    94bbbb3c-2e1f-4546-a7a6-49bbc8aa6936           MiraBamba#1999   
25    94bbbb3c-2e1f-4546-a7a6-49bbc8aa6936          RayzenSama#6999   
26    94bbbb3c-2e1f-4546-a7a6-49bbc8aa6936          RickNagano#8889   
27    94bbbb3c-2e1f-4546-a7a6-49bbc8aa6936            SEN noção#jao   
28    94bbbb3c-2e1f-4546-a7a6-49bbc8aa6936            andderst#4675   
29    94bbbb3c-2e1f-4546-a7a6-49bbc8aa6936                dreyX#low   
30    06b77f0e-32a3-4088-aebb-145ced489229     Cap Nascimento#Capta   
31    06b77f0e-32a3-4088-aebb-145ced489229           DeviceNet#1561   
32    06b77f0e-32a3-4088-aebb-145ced489229        Luiz Peniche#7578   
33    06b77f0e-32a3-4088-aebb-145ced489229                M1ope#BR1   
34    06b77f0e-32a3-4088-aebb-145ced489229             MAGUILA#6386   
35    06b77f0e-32a3-4088-aebb-145ced489229          RayzenSama#6999   
36    06b77f0e-32a3-4088-aebb-145ced489229               Sodo#gh0st   
37    06b77f0e-32a3-4088-aebb-145ced489229              Soneca#7216   
38    06b77f0e-32a3-4088-aebb-145ced489229    gatinha manhosa#rsrsr   
39    06b77f0e-32a3-4088-aebb-145ced489229               pepe#48978   
40    259a5a1e-e0a8-420f-97bd-6e2411640b46              Carlos#0000   
41    259a5a1e-e0a8-420f-97bd-6e2411640b46            Ch4myto#12345   
42    259a5a1e-e0a8-420f-97bd-6e2411640b46               DEIVI#7066   
43    259a5a1e-e0a8-420f-97bd-6e2411640b46       Gato de bolas#lulu   
44    259a5a1e-e0a8-420f-97bd-6e2411640b46      JacintøØPintø#Rilar   
45    259a5a1e-e0a8-420f-97bd-6e2411640b46        Oreia Games#oreia   
46    259a5a1e-e0a8-420f-97bd-6e2411640b46          RayzenSama#6999   
47    259a5a1e-e0a8-420f-97bd-6e2411640b46        mariopesadão#9240   
48    259a5a1e-e0a8-420f-97bd-6e2411640b46           otakubr16#6420   
49    259a5a1e-e0a8-420f-97bd-6e2411640b46                r4m0s#BR1   
50    5e54de80-9c49-458b-9e15-1d5ed1b200c4           LótusWhite#BR1   
51    5e54de80-9c49-458b-9e15-1d5ed1b200c4            Malukaum#9310   
52    5e54de80-9c49-458b-9e15-1d5ed1b200c4         Marcostelão#Tzão   
53    5e54de80-9c49-458b-9e15-1d5ed1b200c4             RUPTURA#9996   
54    5e54de80-9c49-458b-9e15-1d5ed1b200c4          RayzenSama#6999   
55    5e54de80-9c49-458b-9e15-1d5ed1b200c4                